# 509 Final Project

The notebook is for Exploratory Data Analysis (EDA), text data preprocessing, modeling, and evaluation.

## Globally import libraries

In [1]:
from collections import defaultdict, Counter
import datetime as dt
import emoji
import itertools
import matplotlib.pyplot as plt
import numpy as np
import os
import pandas as pd
import pickle
import random
import re
import regex as rex
import requests
import shutil
from string import punctuation
import time
from tqdm import tqdm

import nltk
from nltk.corpus import stopwords

import spacy

from skopt import BayesSearchCV
from skopt.space import Real, Categorical, Integer

from sklearn.feature_extraction.text import TfidfTransformer, \
CountVectorizer, TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.pipeline import make_pipeline, Pipeline
from sklearn import metrics
from sklearn.metrics import make_scorer, f1_score, classification_report, \
confusion_matrix, ConfusionMatrixDisplay, RocCurveDisplay

import textacy.preprocessing as tprep
from textacy.extract import keyword_in_context

# Set pandas global options
pd.options.display.max_rows = 17
pd.options.display.precision = 4
np.set_printoptions(suppress=True, precision=4)

%matplotlib inline

## Upload data from CSV

In [2]:
'''Dir nav citation:
https://softhints.com/python-change-directory-parent/'''
curr_dir = os.path.abspath(os.curdir)
print(curr_dir)
os.chdir("..")
up1_dir = os.path.abspath(os.curdir)
print(up1_dir)

C:\Users\acarr\Documents\GitHub\599_team_project\deliverables
C:\Users\acarr\Documents\GitHub\599_team_project


In [3]:
# change `data_location` to the location of the folder on your machine.
data_location = 'data'

file_in_name01 = 'data_scraped_amc_2023-07-10_13-41-28670390.csv'
file_in_name02 = 'master_business_TheHill.csv'

file_in_path01 = os.path.join(up1_dir, data_location, file_in_name01)
file_in_path02 = os.path.join(up1_dir, data_location, file_in_name02)

print(f'CSV file 1 in path: {file_in_path01}')
print(f'CSV file 2 in path: {file_in_path02}')

CSV file 1 in path: C:\Users\acarr\Documents\GitHub\599_team_project\data\data_scraped_amc_2023-07-10_13-41-28670390.csv
CSV file 2 in path: C:\Users\acarr\Documents\GitHub\599_team_project\data\master_business_TheHill.csv


### Review dataframe

In [4]:
slct_tbl_full_df01 = pd.read_csv(file_in_path01)
print(f'Dataframe shape: {slct_tbl_full_df01.shape}')
display(slct_tbl_full_df01.head())

Dataframe shape: (36420, 8)


text_id source_name                                author  \
0        2   USA Today  USA TODAY, Emily DeLetter, USA TODAY   
1        3   USA Today     USA TODAY, Joy Ashford, USA TODAY   
2        5   USA Today                        Tar Heels Wire   
3        6   USA Today                        Roll Tide Wire   
4        7   USA Today                          Celtics Wire   

                                               title  \
0  Tito's launches 'Tito's in a Big Can,' an empt...   
1  Search for missing actor Julian Sands continue...   
2  Four star running back picks Michigan State ov...   
3  Alabama center Charles Bediako signs one-year ...   
4  Ralph Sampson breaks down iconic Boston Celtic...   

                                                 url          publish_date  \
0  https://www.usatoday.com/story/money/food/2023...  2023-06-21T17:37:40Z   
1  https://www.usatoday.com/story/entertainment/c...  2023-06-20T17:36:09Z   
2  https://tarheelswire.usatoday.com/2023/06/24/f...  2023-06-25T03:51:10Z   
3  https://rolltidewire.usatoday.com/2023/06/23/a...  2023-06-23T21:29:24Z   
4  https://celticswire.usatoday.com/2023/06/23/nb...  2023-06-23T11:00:41Z   

                                        article_text  \
0  Have you ever wanted to own your very own keg ...   
1  Over five months after Julian Sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nFour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nAlabama center Cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nRalph Sampson brea...   

                                             content  
0  Have you ever wanted to own your very own keg ...  
1  Over five months after Julian Sandswent missin...  
2  Mack Brown and the UNC football program have b...  
3  Alabama center Charles Bediako was signed to a...  
4  It was one of the most memorable moments in NB...

## Exploratory Data Analysis (EDA)

### Count missing `article_text` feature

The majority of null values appear in the `content` column. There are also several in `author` and one in `article_text`. Neither `content` nor `author` will be used for current modeling efforts, therefore they are not a factor. The one instance with missing article text will be removed.

In [5]:
count_nan = slct_tbl_full_df01.isnull().sum()
 
# printing the number of values present
# in the column
print('Number of NaN values present: ' + str(count_nan))

Number of NaN values present: text_id           0
source_name       0
author          216
title             0
url               0
publish_date      0
article_text      2
content           0
dtype: int64


### Count blank `article_text` feature

In [6]:
print(len(slct_tbl_full_df01[slct_tbl_full_df01['article_text']==None]))
display(slct_tbl_full_df01[slct_tbl_full_df01['article_text'].isna()].head(20))

0


text_id source_name          author  \
20850    22986    Fox News  Fox News Staff   
34174    66130    Fox News  Fox News Staff   

                                         title  \
20850  Mug shots of the week: June 11-17, 2023   
34174  Mug shots of the week: June 18-24, 2023   

                                                     url  \
20850  https://www.foxnews.com/us/mug-shots-week-june...   
34174  https://www.foxnews.com/us/mug-shots-week-june...   

               publish_date article_text  \
20850  2023-06-18T00:00:51Z          NaN   
34174  2023-06-25T00:00:48Z          NaN   

                                                 content  
20850  These mug shots were taken for arrests made th...  
34174  These mug shots were taken for arrests made th...

### Remove missing `article_text` row(s)

In [7]:
'''Drop missing citation:
https://pandas.pydata.org/pandas-docs/stable/reference
/api/pandas.DataFrame.dropna.html#pandas.DataFrame.dropna'''
slct_tbl_full_df02 = slct_tbl_full_df01.dropna(subset=['article_text'])
print(f'Dataframe shape: {slct_tbl_full_df02.shape}')
display(slct_tbl_full_df02.head())

Dataframe shape: (36418, 8)


text_id source_name                                author  \
0        2   USA Today  USA TODAY, Emily DeLetter, USA TODAY   
1        3   USA Today     USA TODAY, Joy Ashford, USA TODAY   
2        5   USA Today                        Tar Heels Wire   
3        6   USA Today                        Roll Tide Wire   
4        7   USA Today                          Celtics Wire   

                                               title  \
0  Tito's launches 'Tito's in a Big Can,' an empt...   
1  Search for missing actor Julian Sands continue...   
2  Four star running back picks Michigan State ov...   
3  Alabama center Charles Bediako signs one-year ...   
4  Ralph Sampson breaks down iconic Boston Celtic...   

                                                 url          publish_date  \
0  https://www.usatoday.com/story/money/food/2023...  2023-06-21T17:37:40Z   
1  https://www.usatoday.com/story/entertainment/c...  2023-06-20T17:36:09Z   
2  https://tarheelswire.usatoday.com/2023/06/24/f...  2023-06-25T03:51:10Z   
3  https://rolltidewire.usatoday.com/2023/06/23/a...  2023-06-23T21:29:24Z   
4  https://celticswire.usatoday.com/2023/06/23/nb...  2023-06-23T11:00:41Z   

                                        article_text  \
0  Have you ever wanted to own your very own keg ...   
1  Over five months after Julian Sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nFour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nAlabama center Cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nRalph Sampson brea...   

                                             content  
0  Have you ever wanted to own your very own keg ...  
1  Over five months after Julian Sandswent missin...  
2  Mack Brown and the UNC football program have b...  
3  Alabama center Charles Bediako was signed to a...  
4  It was one of the most memorable moments in NB...

### Count characters and words for initial review

In [8]:
tqdm.pandas(ncols=50)  # can use tqdm_gui, optional kwargs, etc
# Now you can use `progress_apply` instead of `apply`

# Raw text character and word counts
slct_tbl_full_df02['char_cnt'] = slct_tbl_full_df02['article_text']\
.progress_apply(len)
slct_tbl_full_df02['word_cnt'] = slct_tbl_full_df02['article_text']\
.progress_apply(lambda x: len(x.split()))
display(slct_tbl_full_df02.head())

100%|███| 36418/36418 [00:00<00:00, 597010.66it/s]
<ipython-input-8-083d5dd6801a>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  slct_tbl_full_df02['char_cnt'] = slct_tbl_full_df02['article_text']\
100%|████| 36418/36418 [00:02<00:00, 18051.98it/s]
<ipython-input-8-083d5dd6801a>:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  slct_tbl_full_df02['word_cnt'] = slct_tbl_full_df02['article_text']\


text_id source_name                                author  \
0        2   USA Today  USA TODAY, Emily DeLetter, USA TODAY   
1        3   USA Today     USA TODAY, Joy Ashford, USA TODAY   
2        5   USA Today                        Tar Heels Wire   
3        6   USA Today                        Roll Tide Wire   
4        7   USA Today                          Celtics Wire   

                                               title  \
0  Tito's launches 'Tito's in a Big Can,' an empt...   
1  Search for missing actor Julian Sands continue...   
2  Four star running back picks Michigan State ov...   
3  Alabama center Charles Bediako signs one-year ...   
4  Ralph Sampson breaks down iconic Boston Celtic...   

                                                 url          publish_date  \
0  https://www.usatoday.com/story/money/food/2023...  2023-06-21T17:37:40Z   
1  https://www.usatoday.com/story/entertainment/c...  2023-06-20T17:36:09Z   
2  https://tarheelswire.usatoday.com/2023/06/24/f...  2023-06-25T03:51:10Z   
3  https://rolltidewire.usatoday.com/2023/06/23/a...  2023-06-23T21:29:24Z   
4  https://celticswire.usatoday.com/2023/06/23/nb...  2023-06-23T11:00:41Z   

                                        article_text  \
0  Have you ever wanted to own your very own keg ...   
1  Over five months after Julian Sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nFour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nAlabama center Cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nRalph Sampson brea...   

                                             content  char_cnt  word_cnt  
0  Have you ever wanted to own your very own keg ...      1234       202  
1  Over five months after Julian Sandswent missin...      2310       346  
2  Mack Brown and the UNC football program have b...      2122       307  
3  Alabama center Charles Bediako was signed to a...      2821       404  
4  It was one of the most memorable moments in NB...      1867       245

### Descriptive statistics

Stats are displayed for both categorical and numerical columns. As expected "Fox News" is the most frequent value in `source_name` as the most articles were collected from that news site. The inclusion of "Associated Press" as the mode for `author` identified it as a potential source for skew in the final results, as AP was rated as a "center" source in the AllSide Media Bias Chart. As a result, all articles with an `author` value of "Associated Press" were removed; similarily, articles by "msn" and "Reuters" were also removed. \
For the numerical values, there was a very large range for both character and word counts (80,454 and 14,306, respectively), but also a large delta between the 75% percentile and max (74,920.5 and 13,433, respectively), indicating a distribution with a very long right tail with a very small amount of some extremely long (outlier) articles. As a result, the standard deviation was also quite large relative to the mean. For the current analyses, no additional efforts will be performed to account for outliers, but this will be an examination factor for future expansion/comparative studies.

In [9]:
slct_tbl_full_df02[['source_name',
                    'author',
                    'publish_date',
                    'article_text']].describe(include="O").T

count unique                                                top  \
source_name   36418     18                                             Forbes   
author        36202   7292                               The Associated Press   
publish_date  36418  32841                               2023-06-13T12:26:00Z   
article_text  36418  34247  This content is only available to USA TODAY su...   

              freq  
source_name   7786  
author        1847  
publish_date    25  
article_text    50

In [10]:
slct_tbl_full_df02.describe().T

count        mean         std  min       25%      50%       75%  \
text_id   36418.0  22394.6756  16157.2024  2.0  10617.25  20324.5  29546.75   
char_cnt  36418.0   4857.9974   4571.2885  6.0   2620.00   3827.0   5622.00   
word_cnt  36418.0    780.7046    772.3514  0.0    412.00    612.0    898.00   

              max  
text_id   71592.0  
char_cnt  77022.0  
word_cnt  12122.0

### Display Source counts

In [11]:
print(slct_tbl_full_df02['source_name'].value_counts().to_string())

Forbes                 7786
New York Post          6862
USA Today              6752
ABC News               4858
CNN                    1686
Business Insider       1563
Fox News               1379
CNBC                   1338
NBC News               1111
Breitbart News         1038
Buzzfeed                750
The Washington Post     374
PEOPLE                  245
MSNBC                   225
Vox                     213
Wired                   129
Reuters                  96
msnNOW                   13


### Examine inclusion of "centrist" sources indicated by `author` feature

slct_tbl_full_df02a = slct_tbl_full_df02[slct_tbl_full_df02['author']\
                                         .isin(['msn',
                                                'Associated Press',
                                                'Reuters'])]

display(slct_tbl_full_df02a[slct_tbl_full_df02a['author']=='msn'])

display(slct_tbl_full_df02a.groupby(by=['source_name', 'author']).count())

In [12]:
counter = Counter(slct_tbl_full_df02['author'])

word_cutoff = 5
con_feature_words = set()

for word, count in counter.items():
    if count > word_cutoff:
        con_feature_words.add(word)
        
print(f'''With a word cutoff of {word_cutoff}, we have 
{len(con_feature_words)} words as features in the model.''')
print(con_feature_words)

With a word cutoff of 5, we have 
1233 words as features in the model.
{'Dan DeFrancesco', 'Kimberly Leonard', nan, 'Julie Coleman', 'Paulina Dedaj', 'JOCELYN NOVECK AP National Writer', 'Uwa Ede-Osifo', 'Huileng Tan', 'MARK SHERMAN Associated Press', 'Jonathan Guyer', 'LSU Tigers Wire', 'COLLEEN LONG Associated Press', 'Zach Braziller', 'Negesti Kaudo', 'Matt Levy', 'Bob McManus', 'GRANT PECK Associated Press', 'Meghan Powers', 'USA TODAY, Anthony Robledo, USA TODAY', 'JEFF AMY Associated Press', 'Joel Sherman', 'Clara Ludmir, Contributor, \n Clara Ludmir, Contributor\n https://www.forbes.com/sites/claraludmir-1/', 'Kathianne Boniello', 'Geri Stengel, Contributor, \n Geri Stengel, Contributor\n https://www.forbes.com/sites/geristengel/', 'JILL LAWLESS Associated Press', 'Blake Schuster', 'Nadja Sayej, Contributor, \n Nadja Sayej, Contributor\n https://www.forbes.com/sites/nadjasayej/', 'Emi Tuyetnhi Tran', 'Alex Harring', 'Lee Brown', 'Hasan Chowdhury', 'Chris Eberhart', 'Nicole Narea

### Assign class based on `source_name` and AllSides Media Bias Chart

slct_tbl_full_df03 = slct_tbl_full_df02[~slct_tbl_full_df02['author']\
                                        .isin(['msn',
                                               'Associated Press',
                                               'Reuters'])]
slct_tbl_full_df03 = slct_tbl_full_df03.reset_index()
slct_tbl_full_df03['political_lean'] = 'right'
print(slct_tbl_full_df03.shape)
display(slct_tbl_full_df03.head())
slct_tbl_full_df03.loc[(slct_tbl_full_df03['source_name'] \
                        == 'The Washington Post') \
                       | (slct_tbl_full_df03['source_name'] \
                          == 'CNN'), 'political_lean'] = 'left'

display(slct_tbl_full_df03.head())

display(slct_tbl_full_df03['political_lean'].value_counts())

### Visualize class distribution

There is definitely an imbalance in the number of instances in each class. This is due to Fox News being the most prolific source, whether because they put out a lot more articles or their sites were more consistently available for scraping. This imbalance is not considered extreme and will not be adjusted for within the scope of the current study.

slct_tbl_full_df03['political_lean'].value_counts().plot(kind="bar",
                                                         legend=True,
                                                         figsize=(5,6),
                                                     title='Class distribution')

### Plot word counts

All sources seem to have very similar consolidation of most frequent word counts between 0 and 2,000. However, the two "left" sources (CNN and The Washington Post) seem to be the significant source of the outliers, with a small amount of articles each that have extremely large word counts (*note:* the x-axis range was truncated at 6,000 to make it more readabla--as noted above, there were some articles with word counts greater than 14,000). Given the simialirties between the sources within each class, the differences may correlate to intentional word limitation based on perceived audience desires, but in the very least do add evidence that the sources have been grouped together appropriately.

## Data preprocessing

In [13]:
def uniq_tok(df_col=pd.DataFrame([''])):
    '''Display all unique tokens across all instances'''
    df_cols1 = pd.Series(df_col)

    all_tokens_lst01 = []

    [all_tokens_lst01.append(f) for f in df_cols1]
    all_tokens_lst01 = list(itertools.chain.from_iterable(all_tokens_lst01))
    all_tokens_set01 = set(all_tokens_lst01)
    print(len(sorted(all_tokens_set01)))
    print(sorted(all_tokens_set01))

In [14]:
slct_tbl_full_df03 = slct_tbl_full_df02.copy()
slct_tbl_full_df04 = slct_tbl_full_df03.copy()

### Case-loading

In [15]:
slct_tbl_full_df03['lower'] = slct_tbl_full_df03['article_text']\
.apply(str.lower)

print(slct_tbl_full_df03.shape)
display(slct_tbl_full_df03.head())

(36418, 11)


text_id source_name                                author  \
0        2   USA Today  USA TODAY, Emily DeLetter, USA TODAY   
1        3   USA Today     USA TODAY, Joy Ashford, USA TODAY   
2        5   USA Today                        Tar Heels Wire   
3        6   USA Today                        Roll Tide Wire   
4        7   USA Today                          Celtics Wire   

                                               title  \
0  Tito's launches 'Tito's in a Big Can,' an empt...   
1  Search for missing actor Julian Sands continue...   
2  Four star running back picks Michigan State ov...   
3  Alabama center Charles Bediako signs one-year ...   
4  Ralph Sampson breaks down iconic Boston Celtic...   

                                                 url          publish_date  \
0  https://www.usatoday.com/story/money/food/2023...  2023-06-21T17:37:40Z   
1  https://www.usatoday.com/story/entertainment/c...  2023-06-20T17:36:09Z   
2  https://tarheelswire.usatoday.com/2023/06/24/f...  2023-06-25T03:51:10Z   
3  https://rolltidewire.usatoday.com/2023/06/23/a...  2023-06-23T21:29:24Z   
4  https://celticswire.usatoday.com/2023/06/23/nb...  2023-06-23T11:00:41Z   

                                        article_text  \
0  Have you ever wanted to own your very own keg ...   
1  Over five months after Julian Sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nFour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nAlabama center Cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nRalph Sampson brea...   

                                             content  char_cnt  word_cnt  \
0  Have you ever wanted to own your very own keg ...      1234       202   
1  Over five months after Julian Sandswent missin...      2310       346   
2  Mack Brown and the UNC football program have b...      2122       307   
3  Alabama center Charles Bediako was signed to a...      2821       404   
4  It was one of the most memorable moments in NB...      1867       245   

                                               lower  
0  have you ever wanted to own your very own keg ...  
1  over five months after julian sands went missi...  
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...  
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...  
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...

### Text normalization

#### Create function

In [16]:
def normalize(text):
    text = tprep.normalize.hyphenated_words(text)
    text = tprep.normalize.quotation_marks(text)
    text = tprep.normalize.unicode(text)
    text = tprep.remove.accents(text)
    return text

#### Call function

In [17]:
slct_tbl_full_df03['norm'] = slct_tbl_full_df03['lower'].apply(normalize)

In [18]:
print(slct_tbl_full_df03.shape)
display(slct_tbl_full_df03.head())

for c in range(0,4):
    try:
        print(slct_tbl_full_df03['norm'][c], '\n')
    except:
        print(f'Skip {c}')

(36418, 12)


text_id source_name                                author  \
0        2   USA Today  USA TODAY, Emily DeLetter, USA TODAY   
1        3   USA Today     USA TODAY, Joy Ashford, USA TODAY   
2        5   USA Today                        Tar Heels Wire   
3        6   USA Today                        Roll Tide Wire   
4        7   USA Today                          Celtics Wire   

                                               title  \
0  Tito's launches 'Tito's in a Big Can,' an empt...   
1  Search for missing actor Julian Sands continue...   
2  Four star running back picks Michigan State ov...   
3  Alabama center Charles Bediako signs one-year ...   
4  Ralph Sampson breaks down iconic Boston Celtic...   

                                                 url          publish_date  \
0  https://www.usatoday.com/story/money/food/2023...  2023-06-21T17:37:40Z   
1  https://www.usatoday.com/story/entertainment/c...  2023-06-20T17:36:09Z   
2  https://tarheelswire.usatoday.com/2023/06/24/f...  2023-06-25T03:51:10Z   
3  https://rolltidewire.usatoday.com/2023/06/23/a...  2023-06-23T21:29:24Z   
4  https://celticswire.usatoday.com/2023/06/23/nb...  2023-06-23T11:00:41Z   

                                        article_text  \
0  Have you ever wanted to own your very own keg ...   
1  Over five months after Julian Sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nFour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nAlabama center Cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nRalph Sampson brea...   

                                             content  char_cnt  word_cnt  \
0  Have you ever wanted to own your very own keg ...      1234       202   
1  Over five months after Julian Sandswent missin...      2310       346   
2  Mack Brown and the UNC football program have b...      2122       307   
3  Alabama center Charles Bediako was signed to a...      2821       404   
4  It was one of the most memorable moments in NB...      1867       245   

                                               lower  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                                norm  
0  have you ever wanted to own your very own keg ...  
1  over five months after julian sands went missi...  
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...  
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...  
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...

have you ever wanted to own your very own keg of tito's handmade vodka? now, that dream can become a reality.the vodka brand is launching tito's in a big can, a $200, 128-ounce stainless steel mini cocktail keg. the keg includes an airtight cap, a co2 regulator, stainless steel spear, tap and handle and an extra set of o-rings. it comes empty, but tito's said it can be filled with their own vodka or with anything else.tito's is also releasing tito's in any can, a smaller insulated can-cooler for $30 that also functions as a refillable cup. it can fit both 16-ounce and 12-ounce cans, and converts into a refillable pint tumbler with a leak-proof lid."rebel against canformity," the product's description reads. "because we don't make canned cocktails, pre-mixes, or seltzers. you do."10best:which fast food restaurants will reign supreme? cast your votes nowwhat are americans drinking this summer?tequila, modelo, canned cocktails and non-alcoholic drinksboth products are available for a limi

In [19]:
#text2find_rex = rex.compile(r'[\n]+')
text2find_rex = rex.compile(r'[\S]\.')

test_lst = []
rpl_lst = []

def test(text):
    test_lst.append(text2find_rex.findall(text))
    rpl_lst.append(text2find_rex.sub(lambda match: match.group(0) + ' ', text))
    
slct_tbl_full_df03['norm'].apply(test)

display(slct_tbl_full_df03.head())
print(test_lst[:20])
print(rpl_lst[:20])

text_id source_name                                author  \
0        2   USA Today  USA TODAY, Emily DeLetter, USA TODAY   
1        3   USA Today     USA TODAY, Joy Ashford, USA TODAY   
2        5   USA Today                        Tar Heels Wire   
3        6   USA Today                        Roll Tide Wire   
4        7   USA Today                          Celtics Wire   

                                               title  \
0  Tito's launches 'Tito's in a Big Can,' an empt...   
1  Search for missing actor Julian Sands continue...   
2  Four star running back picks Michigan State ov...   
3  Alabama center Charles Bediako signs one-year ...   
4  Ralph Sampson breaks down iconic Boston Celtic...   

                                                 url          publish_date  \
0  https://www.usatoday.com/story/money/food/2023...  2023-06-21T17:37:40Z   
1  https://www.usatoday.com/story/entertainment/c...  2023-06-20T17:36:09Z   
2  https://tarheelswire.usatoday.com/2023/06/24/f...  2023-06-25T03:51:10Z   
3  https://rolltidewire.usatoday.com/2023/06/23/a...  2023-06-23T21:29:24Z   
4  https://celticswire.usatoday.com/2023/06/23/nb...  2023-06-23T11:00:41Z   

                                        article_text  \
0  Have you ever wanted to own your very own keg ...   
1  Over five months after Julian Sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nFour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nAlabama center Cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nRalph Sampson brea...   

                                             content  char_cnt  word_cnt  \
0  Have you ever wanted to own your very own keg ...      1234       202   
1  Over five months after Julian Sandswent missin...      2310       346   
2  Mack Brown and the UNC football program have b...      2122       307   
3  Alabama center Charles Bediako was signed to a...      2821       404   
4  It was one of the most memorable moments in NB...      1867       245   

                                               lower  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                                norm  
0  have you ever wanted to own your very own keg ...  
1  over five months after julian sands went missi...  
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...  
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...  
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...

[['y.', 'g.', 's.', 'e.', 'p.', 'd.', 's.', 's.', 'o.', 's.', 'h.'], ['y.', 'r.', 'n.', 'e.', 'a.', 'f.', 'd.', 'd.', 'd.', 'w.', 'd.', 's.', 's.', 'y.', 't.', 'y.', 's.'], ['e.', 'y.', 's.', 'g.', 'd.', 's.', 't.', 'c.', 'r.', 'h.', 'g.', 'n.', 's.'], ['e.', 'y.', 's.', 't.', 'a.', '6.', '4.', '1.', 'e.', 'm.', 't.', 'r.', '6.', '6.', '1.', 'e.', 'm.', 'a.', 't.', 'e.', 'y.', 'm.', 'o.', 'k.', 'n.', '5.', 't.', 'm.'], ['e.', 'y.', 'y.', 'r.', 'd.', 's.', 'w.', 'e.', 'i.', 't.', 'k.'], ['e.', 'y.', 'y.', 't.', 'n.', 'n.', 'e.', 's.', 'r.', 'e.', 'c.', 'r.', 'n.', 'g.', 'h.'], ['e.', 'y.', 's.', 's.', 'n.', 's.', 'e.', 's.', 'k.', 'c.', 'r.', 's.', 'k.', 's.', 'c.', 'r.', 'r.', 'a.', 's.', 's.', 'c.', 'r.', 'd.', 'a.', '1.', 't.', 'c.', 'r.', 's.', 'a.', 'e.', 'm.', 'a.', 'a.', 'c.', 'r.', 'd.', 'e.', 'a.', 'c.', 'r.', 'a.', 's.', 'k.', 'n.', 'c.', 'r.', 's.', 's.', 'e.', 'c.', 'r.', 'k.', 'a.', 's.', 'g.', 'n.', 'c.', 'r.', 'a.', 's.', 'n.', 'n.', 'h.', '..', 'c.', 'r.', 'a.', ').', 'e

### Remove special characters

#### Create function

In [20]:
#rex_sep = rex.compile(r'&nbsp;')
#rex_ucode = rex.compile(r'[\\]u20*')

'''re.sub lambda citation:
https://chat.openai.com/share/402ec66e-2802-4cda-af8c-6f9f5b097d85
'''
sep_lst = []
ucode_lst = []
# Add leading and trailing space to URLs
def rex_replace(text):
    text = text.replace(r'&nbsp;', ' ').replace(r'-', ' ')\
    .replace('\u2063', ' ').replace('\u2066', ' ')\
    .replace('\u2069', ' ').replace('\u200b', ' ').replace('\u200d', ' ')\
    .replace('(click to view)', ' ')\
    .replace('a post shared by', ' ')\
    .replace('app users click here', ' ')\
    .replace('app users: click here', ' ')\
    .replace('app users, click here:', ' ')\
    .replace('click here.', ' ')\
    .replace('click here for more cartoons', ' ')\
    .replace('click here for more', ' ')\
    .replace('click here for more sports coverage on foxnews.com', ' ')\
    .replace('click here for other fox news digital adoptable pets stories', ' ')\
    .replace('click here for the fox news app', ' ')\
    .replace('click here for the latest fox news reporting', ' ')\
    .replace('click here for topline and cross tabs conducted', ' ')\
    .replace('click here to hear more', ' ')\
    .replace('click here to ge the fox news app', ' ')\
    .replace('click here to get the fox news app', ' ')\
    .replace('click here to get the opinion newsletter', ' ')\
    .replace('click here to learn more', ' ')\
    .replace('click here to read more', ' ')\
    .replace('click here to sign up for our health newsletter', ' ')\
    .replace('click here to sign up for our lifestyle newsletter', ' ')\
    .replace('click here to sign up for our opinion newsletter', ' ')\
    .replace('click here to sign up for the entertainment newsletter', ' ')\
    .replace('click here to subscribe and get your first year of fox nation free of charge', ' ')\
    .replace('click here to view', ' ')\
    .replace("click to get kurt's cyberguy newsletter with quick tips, tech reviews, security alerts and easy how to's to make you smarter", ' ')\
    .replace("click to get kurt's cyberguy newsletter with security alerts, quick tips, tech reviews, security and easy how to's to make you smarter", ' ')\
    .replace("click to get kurt's free cyberguy newsletter with quick tips, tech reviews, security alerts and easy how to's to make you smarter", ' ')\
    .replace("click to get kurt's free cyberguy newsletter with security alerts, quick tips, tech reviews, and easy how to's to make you smarter", ' ')\
    .replace('click to get the fox news app', ' ')\
    .replace('fox news digital', ' ')\
    .replace('request for comment', ' ')\
    .replace('the ap ', ' ')\
    .replace('copyright © 2023 breitbart', ' ')\
    .replace('all rights reserved', ' ')\
    .replace('copyright 2023 cyberguy.com', ' ')\
    .replace('copyright 2023 fox news network', ' ')\
    .replace('copyright 2023 viq media transcription', ' ')\
    .replace("please let us know if you're having issues with commenting", ' ')\
    .replace('view this post on instagram', ' ')
    return text

#### Call function

In [21]:
slct_tbl_full_df03['trimmed'] = slct_tbl_full_df03['norm'].apply(rex_replace)

In [22]:
print(slct_tbl_full_df03.shape)
display(slct_tbl_full_df03.head())

(36418, 13)


text_id source_name                                author  \
0        2   USA Today  USA TODAY, Emily DeLetter, USA TODAY   
1        3   USA Today     USA TODAY, Joy Ashford, USA TODAY   
2        5   USA Today                        Tar Heels Wire   
3        6   USA Today                        Roll Tide Wire   
4        7   USA Today                          Celtics Wire   

                                               title  \
0  Tito's launches 'Tito's in a Big Can,' an empt...   
1  Search for missing actor Julian Sands continue...   
2  Four star running back picks Michigan State ov...   
3  Alabama center Charles Bediako signs one-year ...   
4  Ralph Sampson breaks down iconic Boston Celtic...   

                                                 url          publish_date  \
0  https://www.usatoday.com/story/money/food/2023...  2023-06-21T17:37:40Z   
1  https://www.usatoday.com/story/entertainment/c...  2023-06-20T17:36:09Z   
2  https://tarheelswire.usatoday.com/2023/06/24/f...  2023-06-25T03:51:10Z   
3  https://rolltidewire.usatoday.com/2023/06/23/a...  2023-06-23T21:29:24Z   
4  https://celticswire.usatoday.com/2023/06/23/nb...  2023-06-23T11:00:41Z   

                                        article_text  \
0  Have you ever wanted to own your very own keg ...   
1  Over five months after Julian Sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nFour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nAlabama center Cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nRalph Sampson brea...   

                                             content  char_cnt  word_cnt  \
0  Have you ever wanted to own your very own keg ...      1234       202   
1  Over five months after Julian Sandswent missin...      2310       346   
2  Mack Brown and the UNC football program have b...      2122       307   
3  Alabama center Charles Bediako was signed to a...      2821       404   
4  It was one of the most memorable moments in NB...      1867       245   

                                               lower  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                                norm  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                             trimmed  
0  have you ever wanted to own your very own keg ...  
1  over five months after julian sands went missi...  
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...  
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...  
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...

'''Complex citation (add lambda):
https://chat.openai.com/share/a135754c-c38c-47ea-8f83-54d41d5397ab
'''
slct_tbl_full_df03['trimmed'] = slct_tbl_full_df03['norm'].apply(lambda x: x.replace('&nbsp;', ' ').replace(r'\n', ' ').replace('\u2063', ' ').replace('\u2066', ' ').replace('\u2069', ' ').replace('\u200b', ' ').replace('\u200d', ' '))

### Separate emojis as individual tokens

#### Create function

In [23]:
def emoji_split(text):
    return("".join([' ' + c + ' ' if emoji.is_emoji(c) else c for c in text]))

#### Call function

In [24]:
slct_tbl_full_df03['emoji_split'] = slct_tbl_full_df03['trimmed']\
.apply(emoji_split)

print(slct_tbl_full_df03.shape)
display(slct_tbl_full_df03.head())

for c in range(0,1):
    try:
        print(slct_tbl_full_df03['emoji_split'][c], '\n')
    except:
        print(f'Skip {c}')

(36418, 14)


text_id source_name                                author  \
0        2   USA Today  USA TODAY, Emily DeLetter, USA TODAY   
1        3   USA Today     USA TODAY, Joy Ashford, USA TODAY   
2        5   USA Today                        Tar Heels Wire   
3        6   USA Today                        Roll Tide Wire   
4        7   USA Today                          Celtics Wire   

                                               title  \
0  Tito's launches 'Tito's in a Big Can,' an empt...   
1  Search for missing actor Julian Sands continue...   
2  Four star running back picks Michigan State ov...   
3  Alabama center Charles Bediako signs one-year ...   
4  Ralph Sampson breaks down iconic Boston Celtic...   

                                                 url          publish_date  \
0  https://www.usatoday.com/story/money/food/2023...  2023-06-21T17:37:40Z   
1  https://www.usatoday.com/story/entertainment/c...  2023-06-20T17:36:09Z   
2  https://tarheelswire.usatoday.com/2023/06/24/f...  2023-06-25T03:51:10Z   
3  https://rolltidewire.usatoday.com/2023/06/23/a...  2023-06-23T21:29:24Z   
4  https://celticswire.usatoday.com/2023/06/23/nb...  2023-06-23T11:00:41Z   

                                        article_text  \
0  Have you ever wanted to own your very own keg ...   
1  Over five months after Julian Sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nFour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nAlabama center Cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nRalph Sampson brea...   

                                             content  char_cnt  word_cnt  \
0  Have you ever wanted to own your very own keg ...      1234       202   
1  Over five months after Julian Sandswent missin...      2310       346   
2  Mack Brown and the UNC football program have b...      2122       307   
3  Alabama center Charles Bediako was signed to a...      2821       404   
4  It was one of the most memorable moments in NB...      1867       245   

                                               lower  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                                norm  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                             trimmed  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                         emoji_split  
0  have you ever wanted to own your very own keg ...  
1  over five months after julian sands went missi...  
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...  
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...  
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...

have you ever wanted to own your very own keg of tito's handmade vodka? now, that dream can become a reality.the vodka brand is launching tito's in a big can, a $200, 128 ounce stainless steel mini cocktail keg. the keg includes an airtight cap, a co2 regulator, stainless steel spear, tap and handle and an extra set of o rings. it comes empty, but tito's said it can be filled with their own vodka or with anything else.tito's is also releasing tito's in any can, a smaller insulated can cooler for $30 that also functions as a refillable cup. it can fit both 16 ounce and 12 ounce cans, and converts into a refillable pint tumbler with a leak proof lid."rebel against canformity," the product's description reads. "because we don't make canned cocktails, pre mixes, or seltzers. you do."10best:which fast food restaurants will reign supreme? cast your votes nowwhat are americans drinking this summer?tequila, modelo, canned cocktails and non alcoholic drinksboth products are available for a limi

### Remove URLs

#### Create function

In [25]:
rex_url_c = rex.compile(r'http[s]?:[\/]+[\S]*\s')

'''re.sub lambda citation:
https://chat.openai.com/share/402ec66e-2802-4cda-af8c-6f9f5b097d85
'''
# Add leading and trailing space to URLs
def remove_url(text):
    text = rex_url_c.sub(r' ', text)
    return text

#### Call function

In [26]:
slct_tbl_full_df03['urls_removed'] = slct_tbl_full_df03['emoji_split'].apply(remove_url)

In [27]:
print(slct_tbl_full_df03.shape)
display(slct_tbl_full_df03.head())

(36418, 15)


text_id source_name                                author  \
0        2   USA Today  USA TODAY, Emily DeLetter, USA TODAY   
1        3   USA Today     USA TODAY, Joy Ashford, USA TODAY   
2        5   USA Today                        Tar Heels Wire   
3        6   USA Today                        Roll Tide Wire   
4        7   USA Today                          Celtics Wire   

                                               title  \
0  Tito's launches 'Tito's in a Big Can,' an empt...   
1  Search for missing actor Julian Sands continue...   
2  Four star running back picks Michigan State ov...   
3  Alabama center Charles Bediako signs one-year ...   
4  Ralph Sampson breaks down iconic Boston Celtic...   

                                                 url          publish_date  \
0  https://www.usatoday.com/story/money/food/2023...  2023-06-21T17:37:40Z   
1  https://www.usatoday.com/story/entertainment/c...  2023-06-20T17:36:09Z   
2  https://tarheelswire.usatoday.com/2023/06/24/f...  2023-06-25T03:51:10Z   
3  https://rolltidewire.usatoday.com/2023/06/23/a...  2023-06-23T21:29:24Z   
4  https://celticswire.usatoday.com/2023/06/23/nb...  2023-06-23T11:00:41Z   

                                        article_text  \
0  Have you ever wanted to own your very own keg ...   
1  Over five months after Julian Sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nFour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nAlabama center Cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nRalph Sampson brea...   

                                             content  char_cnt  word_cnt  \
0  Have you ever wanted to own your very own keg ...      1234       202   
1  Over five months after Julian Sandswent missin...      2310       346   
2  Mack Brown and the UNC football program have b...      2122       307   
3  Alabama center Charles Bediako was signed to a...      2821       404   
4  It was one of the most memorable moments in NB...      1867       245   

                                               lower  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                                norm  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                             trimmed  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                         emoji_split  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                        urls_removed  
0  have you ever wanted to own your very own keg ...  
1  over five months after julian sands went missi...  
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...  
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...  
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...

In [28]:
source_name_lst = slct_tbl_full_df03['source_name'].unique()
print(source_name_lst)

for s in source_name_lst:
    df01 = slct_tbl_full_df03.loc[slct_tbl_full_df03['source_name'] == s]
    df01 = df01.reset_index()
    counter = 0
    for c in range(0,6):
        counter += 1
        print(f'{s} article #{counter}')
        try:
            print('URL:', df01['url'][c])
            print('Author(s):', df01['author'][c])
            print('Title:', df01['title'][c])
            print(df01['urls_removed'][c], '\n')
        except:
            print(f'Skip {c}')

['USA Today' 'ABC News' 'CNN' 'Business Insider' 'Breitbart News' 'MSNBC'
 'Buzzfeed' 'Wired' 'NBC News' 'The Washington Post' 'Fox News' 'Reuters'
 'New York Post' 'Forbes' 'PEOPLE' 'CNBC' 'Vox' 'msnNOW']
USA Today article #1
URL: https://www.usatoday.com/story/money/food/2023/06/21/titos-vodka-keg-price/70342132007/
Author(s): USA TODAY, Emily DeLetter, USA TODAY
Title: Tito's launches 'Tito's in a Big Can,' an empty cocktail keg listed at $200
have you ever wanted to own your very own keg of tito's handmade vodka? now, that dream can become a reality.the vodka brand is launching tito's in a big can, a $200, 128 ounce stainless steel mini cocktail keg. the keg includes an airtight cap, a co2 regulator, stainless steel spear, tap and handle and an extra set of o rings. it comes empty, but tito's said it can be filled with their own vodka or with anything else.tito's is also releasing tito's in any can, a smaller insulated can cooler for $30 that also functions as a refillable cup. it 

### Remove returns and tabs

#### Create function

In [29]:
rex_tabs = rex.compile(r'[\t]+')
rex_returns = rex.compile(r'[\n]+')
rex_errant_returns = rex.compile(r'[\n][\s]+[\n]')
rex_numbers = rex.compile(r'[\d]+')
rex_periods = rex.compile(r'[\S]\.')

def remove_returns(text):
    repl_text = rex_tabs.sub(r' ', text)
    repl_text = rex_returns.sub(r'\n', repl_text)
    repl_text = rex_errant_returns.sub(r'\n', repl_text)
    repl_text = rex_numbers.sub(r' ', repl_text)
    repl_text = rex_periods.sub(lambda match: match.group(0) + ' ', repl_text)
    #repl_text = rex_periods.sub(r'\. ', repl_text)
    return repl_text

#### Call function

In [30]:
slct_tbl_full_df03['w_one_return'] = slct_tbl_full_df03['urls_removed'].apply(remove_returns)

In [31]:
source_name_lst = slct_tbl_full_df03['source_name'].unique()
print(source_name_lst)

print(slct_tbl_full_df03.shape)
display(slct_tbl_full_df03.head())

for s in source_name_lst:
    df01 = slct_tbl_full_df03.loc[slct_tbl_full_df03['source_name'] == s]
    df01 = df01.reset_index()
    counter = 0
    for c in range(0,6):
        counter += 1
        print(f'{s} article #{counter}')
        try:
            print('URL:', df01['url'][c])
            print('Author(s):', df01['author'][c])
            print('Title:', df01['title'][c])
            print(df01['w_one_return'][c], '\n')
        except:
            print(f'Skip {c}')

['USA Today' 'ABC News' 'CNN' 'Business Insider' 'Breitbart News' 'MSNBC'
 'Buzzfeed' 'Wired' 'NBC News' 'The Washington Post' 'Fox News' 'Reuters'
 'New York Post' 'Forbes' 'PEOPLE' 'CNBC' 'Vox' 'msnNOW']
(36418, 16)


text_id source_name                                author  \
0        2   USA Today  USA TODAY, Emily DeLetter, USA TODAY   
1        3   USA Today     USA TODAY, Joy Ashford, USA TODAY   
2        5   USA Today                        Tar Heels Wire   
3        6   USA Today                        Roll Tide Wire   
4        7   USA Today                          Celtics Wire   

                                               title  \
0  Tito's launches 'Tito's in a Big Can,' an empt...   
1  Search for missing actor Julian Sands continue...   
2  Four star running back picks Michigan State ov...   
3  Alabama center Charles Bediako signs one-year ...   
4  Ralph Sampson breaks down iconic Boston Celtic...   

                                                 url          publish_date  \
0  https://www.usatoday.com/story/money/food/2023...  2023-06-21T17:37:40Z   
1  https://www.usatoday.com/story/entertainment/c...  2023-06-20T17:36:09Z   
2  https://tarheelswire.usatoday.com/2023/06/24/f...  2023-06-25T03:51:10Z   
3  https://rolltidewire.usatoday.com/2023/06/23/a...  2023-06-23T21:29:24Z   
4  https://celticswire.usatoday.com/2023/06/23/nb...  2023-06-23T11:00:41Z   

                                        article_text  \
0  Have you ever wanted to own your very own keg ...   
1  Over five months after Julian Sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nFour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nAlabama center Cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nRalph Sampson brea...   

                                             content  char_cnt  word_cnt  \
0  Have you ever wanted to own your very own keg ...      1234       202   
1  Over five months after Julian Sandswent missin...      2310       346   
2  Mack Brown and the UNC football program have b...      2122       307   
3  Alabama center Charles Bediako was signed to a...      2821       404   
4  It was one of the most memorable moments in NB...      1867       245   

                                               lower  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                                norm  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                             trimmed  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                         emoji_split  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                        urls_removed  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   
2  \n\n\n\n\n\n\n\n\n\n\n\n\n\nfour star running ...   
3  \n\n\n\n\n\n\n\n\n\n\n\n\n\nalabama center cha...   
4  \n\n\n\n\n\n\n\n\n\n\n\n\n\nralph sampson brea...   

                                        w_one_return  
0  have you ever wanted to own your very own keg ...  
1  over five months after julian sands went missi...  
2  \nfour star running back picks michigan state ...  
3  \nalabama center charles bediako signs one yea...  
4  \nralph sampson breaks down iconic boston celt...

USA Today article #1
URL: https://www.usatoday.com/story/money/food/2023/06/21/titos-vodka-keg-price/70342132007/
Author(s): USA TODAY, Emily DeLetter, USA TODAY
Title: Tito's launches 'Tito's in a Big Can,' an empty cocktail keg listed at $200
have you ever wanted to own your very own keg of tito's handmade vodka? now, that dream can become a reality. the vodka brand is launching tito's in a big can, a $ ,   ounce stainless steel mini cocktail keg.  the keg includes an airtight cap, a co  regulator, stainless steel spear, tap and handle and an extra set of o rings.  it comes empty, but tito's said it can be filled with their own vodka or with anything else. tito's is also releasing tito's in any can, a smaller insulated can cooler for $  that also functions as a refillable cup.  it can fit both   ounce and   ounce cans, and converts into a refillable pint tumbler with a leak proof lid. "rebel against canformity," the product's description reads.  "because we don't make canned cocktail

### Calculate concentration ratio of each set of corpora

In [32]:
# Capstone note: Extended custom function to use bi- and tri-grams
def concen_ratio(header_lst=[],
                 token_lsts=[],
                 ng_start=1,
                 ng_end=1):
    lyr_corp_lst = []
    for l in token_lsts:
        #print(type(l))
        lyr_corp_lst.append(' '.join(l))
    #print(len(lyr_corp_lst))
    #print(lyr_corp_lst)

    cv = CountVectorizer(input='content',
                         encoding='utf-8',
                         stop_words=None,
                         token_pattern=r'\S+',
                         ngram_range=(ng_start, ng_end)
                        )

    lyr_tokens_fit = cv.fit(lyr_corp_lst)
    
    try:
        print(pd.Series(cv.get_feature_names()).sample(15))
    except:
        pass

    lyr_tokens_sm = cv.transform(lyr_corp_lst)
    display(lyr_tokens_sm)

    df = pd.DataFrame(lyr_tokens_sm.toarray(),
                      columns=cv.get_feature_names())
    #display(df)

    df02 = df.copy()
    df02['r_sum'] = df02.sum(axis=1)
    #display(df02)

    '''Filter by frequency for all columns citation:
    OpenAI. (2021). ChatGPT [Computer software]. https://openai.com/;
    https://pandas.pydata.org/pandas-docs/stable/reference/api/
    pandas.DataFrame.ge.html'''
    condition = df.ge(5).all()
    #print(condition)

    # Get the list of columns that satisfy the condition
    columns = condition[condition].index.tolist()
    #print(columns)
    columns.append('r_sum')
    #print(columns)

    #display(df02[columns])

    df03 = df02[columns].copy()
    display(df03)

    '''Filter by frequency for all columns & add summary row citation:
    OpenAI. (2021). ChatGPT [Computer software]. https://openai.com/'''
    df04 = df03.apply(lambda x: x / df03.iloc[:,-1], axis=0)
    #display(df04)

    # Create new rows by dividing one artist row by the second artists row
    new_row01 = df04.iloc[0] / df04.iloc[1]
    new_row02 = df04.iloc[1] / df04.iloc[0]

    # Append the new row to the DataFrame
    df04 = df04.append(new_row01, ignore_index=True)
    df04 = df04.append(new_row02, ignore_index=True)
    display(df04)

    # Transpose dataframe
    df05 = df04.T
    df05 = df05.reset_index()
    df05.columns = ['token',
                    'c1_concen',
                    'c2_concen',
                    'c1c2_concen_ratio',
                    'c2c1_concen_ratio']
    #print(df05)
    
    '''Sort values citation:
    https://pandas.pydata.org/pandas-docs/stable/reference/api
    /pandas.DataFrame.sort_values.html'''
    print(header_lst[0])
    display(df05[['token',
                  'c1c2_concen_ratio']].sort_values(by='c1c2_concen_ratio',
                                                    ascending=False).head(10))
    print(header_lst[1])
    display(df05[['token',
                  'c2c1_concen_ratio']].sort_values(by='c2c1_concen_ratio',
                                                    ascending=False).head(10))

def run_cr(df=pd.DataFrame(),
           ref_lst=[],
           token_col=None,
           ref_col=None):
    df01 = df.copy()
    df01['token_split'] = df01[token_col].progress_apply(str.split)
    for i in ref_lst:
        df01a = df01[df01[ref_col] == i]
        print(df01a.shape)
        display(df01a.head(2))
        df01a_s1 = list(itertools.chain.from_iterable(list(pd.Series(df01a['token_split']))))
        print(df01a_s1[:2])

        df01b = df01[df01[ref_col] != i]
        print(df01b.shape)
        display(df01b.head(2))
        df01b_s1 = list(itertools.chain.from_iterable(list(pd.Series(df01b['token_split']))))
        print(df01b_s1[:1])
        for n in range(4,6):
            concen_ratio(header_lst=[f'1({i})-to-all', f'all-to-1({i})'],
                         token_lsts=[df01a_s1, df01b_s1],
                         ng_start=n,
                         ng_end=n)

In [33]:
run_cr(df=slct_tbl_full_df03,
       ref_lst=source_name_lst[:],
       token_col='w_one_return',
       ref_col='source_name')

100%|████| 36418/36418 [00:02<00:00, 12291.06it/s]


(6752, 17)


text_id source_name                                author  \
0        2   USA Today  USA TODAY, Emily DeLetter, USA TODAY   
1        3   USA Today     USA TODAY, Joy Ashford, USA TODAY   

                                               title  \
0  Tito's launches 'Tito's in a Big Can,' an empt...   
1  Search for missing actor Julian Sands continue...   

                                                 url          publish_date  \
0  https://www.usatoday.com/story/money/food/2023...  2023-06-21T17:37:40Z   
1  https://www.usatoday.com/story/entertainment/c...  2023-06-20T17:36:09Z   

                                        article_text  \
0  Have you ever wanted to own your very own keg ...   
1  Over five months after Julian Sands went missi...   

                                             content  char_cnt  word_cnt  \
0  Have you ever wanted to own your very own keg ...      1234       202   
1  Over five months after Julian Sandswent missin...      2310       346   

                                               lower  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   

                                                norm  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   

                                             trimmed  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   

                                         emoji_split  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   

                                        urls_removed  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   

                                        w_one_return  \
0  have you ever wanted to own your very own keg ...   
1  over five months after julian sands went missi...   

                                         token_split  
0  [have, you, ever, wanted, to, own, your, very,...  
1  [over, five, months, after, julian, sands, wen...

['have', 'you']
(29666, 17)


text_id source_name                                          author  \
9        22    ABC News                                     Teddy Grant   
28       59    ABC News  THALIA BEATY and GLENN GAMBOA Associated Press   

                                                title  \
9   Washington passes California as most expensive...   
28  Rage giving prompted by the end of Roe has dro...   

                                                  url          publish_date  \
9   https://abcnews.go.com/US/washington-passes-ca...  2023-06-22T01:27:39Z   
28  https://abcnews.go.com/Politics/wireStory/rage...  2023-06-24T07:34:26Z   

                                         article_text  \
9   Washington passes California as most expensive...   
28  'Rage giving' prompted by the end of Roe has d...   

                                              content  char_cnt  word_cnt  \
9   Washington state has overtaken California as t...      2784       467   
28  The rage giving did not last. Abortion access ...      8326      1287   

                                                lower  \
9   washington passes california as most expensive...   
28  'rage giving' prompted by the end of roe has d...   

                                                 norm  \
9   washington passes california as most expensive...   
28  'rage giving' prompted by the end of roe has d...   

                                              trimmed  \
9   washington passes california as most expensive...   
28  'rage giving' prompted by the end of roe has d...   

                                          emoji_split  \
9   washington passes california as most expensive...   
28  'rage giving' prompted by the end of roe has d...   

                                         urls_removed  \
9   washington passes california as most expensive...   
28  'rage giving' prompted by the end of roe has d...   

                                         w_one_return  \
9   washington passes california as most expensive...   
28  'rage giving' prompted by the end of roe has d...   

                                          token_split  
9   [washington, passes, california, as, most, exp...  
28  ['rage, giving', prompted, by, the, end, of, r...

...

r_sum
0    1.0
1    1.0
2    1.0
3    1.0

1(msnNOW)-to-all


token  c1c2_concen_ratio
0  r_sum                1.0

all-to-1(msnNOW)


token  c2c1_concen_ratio
0  r_sum                1.0

### KWIC

def kwic(doc_series, keyword, window=35, print_samples=5):
    '''Search article text for keywords in context (KWIC)'''
    def add_kwic(text):
        kwic_list.extend(keyword_in_context(doc=text,
                                            keyword=keyword,
                                            ignore_case=True,
                                            window_width=window))
    kwic_list = []
    doc_series.map(add_kwic)
    
    if print_samples is None or print_samples==0:
        return kwic_list
    else:
        k = min(print_samples, len(kwic_list))
        print(f"{k} random samples out of {len(kwic_list)}" + \
              f" contexts for '{keyword}':")
        for sample in random.sample(list(kwic_list), k):
            display(re.sub(r'[\n\t]', ' ', sample[0]) + ' ' +\
                  sample[1] + ' ' +\
                  re.sub(r'[\n\t]', ' ', sample[2]))

In [55]:
def kwic(doc_series, keyword, window=35, print_samples=5):
    '''Search article text for keywords in context (KWIC)'''
    def add_kwic(text):
        kwic_list.extend(keyword_in_context(doc=text,
                                            keyword=keyword,
                                            ignore_case=True,
                                            window_width=window))
    kwic_list = []
    doc_series.map(add_kwic)
    
    if print_samples is None or print_samples==0:
        return kwic_list
    else:
        k = min(print_samples, len(kwic_list))
        print(f"{k} random samples out of {len(kwic_list)}" + \
              f" contexts for '{keyword}':")
        for sample in random.sample(list(kwic_list), k):
            display(sample[0] + sample[1] + sample[2])
            print('\n')

In [57]:
#kwic(slct_tbl_full_df03['article_text'], 'amp', window=150, print_samples=120)

kwic(slct_tbl_full_df03['norm'],
     'your inbox every morning',
     window=2000,
     print_samples=500)

500 random samples out of 5314 contexts for 'your inbox every morning':


"ose games (11.1%).\nin 33.3% of his games this year (21 of 63), he has notched at least one rbi. in six of those games (9.5%) he recorded more than one rbi, while he was responsible for three or more of his team's runs in one contest.\nfrance has struck out at least once in 49.2% of his games this season (31 of 63), with two or more strikeouts in eight of them (12.7%).\n\nty france stats against the marlins\n\n\n\n\ndate\nopp. sp\nh/ab\nxbh\nhr\nrbi\nr\nk/bb\nsb\n\n\n\n\n5/1/2022\nsandy alcantara\n1-for-4\n0\n0\n0\n1\n2/0\n0\n\n\n4/30/2022\njesus luzardo\n0-for-4\n0\n0\n0\n0\n0/0\n0\n\n\n4/29/2022\nelieser hernandez\n1-for-5\n0\n0\n0\n0\n0/0\n0\n\n\n\n\nplace your legal, online sports bets in co and nj at tipico sportsbook now.\nmarlins starter: jesus luzardo\n\nluzardo toes the rubber for the marlins in his 14th of the season. he is 5-4 with a 3.79 era and 86 ks in 73 2/3 innings pitched.\nthe lefty last pitched on tuesday against the kansas city royals, when he lasted seven innings,

'war in 1946, where he would see a face that would become quite familiar in his later life.\nbuy celtics tickets\nit just so happened to be coached by a one red auerbach, later to be his coach in boston as well.\n\n\n\n\n\n\nhappy birthday in heaven john mahnken! #celtics pic.twitter.com/fsuef0drcv\n— honest☘️larry (@honestlarry1) june 16, 2021\n\nmahnken would be traded a total of five times before landing with the celtics in 1951 for the first multi-season stretch of his career since it began.\nhe spent four seasons total playing for boston, recording 3.6 points, 2.9 rebounds, and 1.3 assists per game.\nit would be the last stop of a seven-season career pre-dating even the baa, after which mahnken would virtually disappear from professional basketball circles until shortly before he passed in 2000.\n\n\n \n\n\n\n\nit is also the day that former team minority owner louis pieri left us in 1967,\n\n1959-1960 boston celtics (seated l-r): frank ramsey, bob cousy, coach red auerbach, pres.

'\t\t\t\n\n\n\n \n\t\t\t\tlink\t\t\t\n\n\n\n \n\n\n\n\n \n\t\t\t\ton facebook\t\t\t\n\n\n\n \n\t\t\t\ton twitter\t\t\t\n\n\n\n \n\t\t\t\tvia text message\t\t\t\n\n\n\n \n\t\t\t\ton linkedin\t\t\t\n\n\n\n \n\t\t\t\tvia email\t\t\t\n\n\n\n \n\t\t\t\thttps://seahawkswire.usatoday.com/2023/06/30/nfc-west-watch-rams-sign-cb-ahkello-witherspoon/\t\t\t\n\n\n\n\n\n\n\n\n\n\nkole musgrove \n\n\n\njune 30, 2023 11:15 am pt\n\n\n\n\n\n\n\n\n\nthe seattle seahawks\' division rivals, the los angeles rams, are in the midst of a reboot. after having unequivocally the worst championship defense season in the history of the nfl, a reset is what they desperately need.\nwith a reset comes new faces, especially in the secondary after trading away cornerback jalen ramsey. one new face is rather recent, as they just signed cornerback ahkello witherspoon.\n\nfree agent cb ahkello witherspoon is signing with the #rams, per source. \nat 6-2, 208 pounds, witherspoon\'s a big corner who\'s been very productive. 

"out on multiple occasions in 25.8% of games (16 times).\n\ntaylor ward stats against the rangers\n\n\n\n\ndate\nopp. sp\nh/ab\nxbh\nhr\nrbi\nr\nk/bb\nsb\n\n\n\n\n6/12/2023\ndane dunning\n2-for-5\n1\n0\n0\n3\n1/1\n0\n\n\n5/7/2023\nmartin perez\n1-for-3\n0\n0\n1\n1\n0/2\n0\n\n\n5/6/2023\nnathan eovaldi\n1-for-4\n0\n0\n0\n0\n0/0\n0\n\n\n5/5/2023\ndane dunning\n0-for-4\n0\n0\n0\n1\n1/0\n0\n\n\n10/2/2022\ntyson miller\n3-for-4\n0\n0\n1\n2\n0/0\n0\n\n\n10/1/2022\ncole ragans\n0-for-4\n0\n0\n0\n0\n2/0\n0\n\n\n9/30/2022\nglenn otto\n2-for-4\n2\n0\n1\n0\n1/0\n0\n\n\n9/22/2022\nmartin perez\n1-for-4\n0\n0\n1\n0\n1/0\n0\n\n\n9/21/2022\ndane dunning\n1-for-3\n1\n1\n2\n1\n1/1\n0\n\n\n9/20/2022\ncole ragans\n2-for-4\n1\n0\n1\n2\n1/0\n0\n\n\n\n\nplace your legal, online sports bets in co and nj at tipico sportsbook now.\nrangers starter: jon gray\n\ngray takes the hill for the rangers in his 13th of the season. he is 6-2 with a 2.32 era and 63 ks through 73 2/3 innings pitched.\nthe righty's last ap

...

'tats against the pirates\n\n\n\n\ndate\nopp. sp\nh/ab\nxbh\nhr\nrbi\nr\nk/bb\nsb\n\n\n\n\n8/24/2022\nmitch keller\n2-for-4\n1\n0\n3\n2\n0/1\n0\n\n\n8/23/2022\njt brubaker\n1-for-4\n0\n0\n1\n0\n2/0\n0\n\n\n8/22/2022\nroansy contreras\n0-for-4\n0\n0\n0\n0\n0/0\n0\n\n\n6/12/2022\njose quintana\n1-for-4\n1\n0\n0\n0\n0/0\n0\n\n\n6/11/2022\nzach thompson\n2-for-4\n0\n0\n3\n1\n0/0\n0\n\n\n6/10/2022\nroansy contreras\n3-for-4\n1\n1\n2\n1\n1/0\n0\n\n\n6/9/2022\njt brubaker\n1-for-4\n0\n0\n1\n1\n2/0\n0\n\n\n7/7/2021\nwil crowe\n3-for-5\n1\n0\n1\n2\n1/1\n1\n\n\n7/6/2021\nchad kuhl\n0-for-3\n0\n0\n0\n0\n1/1\n0\n\n\n7/5/2021\nchase de jong\n1-for-4\n0\n0\n0\n0\n2/0\n0\n\n\n\n\nplace your legal, online sports bets in co and nj at tipico sportsbook now.\npirates starter: luis ortiz\n\nortiz gets the start for the pirates in his sixth of the season. he holds a record of 1-2 with a 4.23 era and 16 ks in 27 2/3 innings pitched.\nin his most recent appearance out of the pen on wednesday, the right-hande

"247sports.com.\nhe has something in common with every other quarterback addition made by the new staff this far, however. he's from the state of texas.\nhere are the five quarterbacks to join or commit to the wisconsin program since phil longo was hired and how they're tied together. it's a trend worth noting as we move deeper into the fickell/longo era in madison.\n\n\nsenior tanner mordecai (transfer)\n\n\nwisconsin quarterback tanner mordecai (8) is shown during practice tuesday, april 11, 2023 at camp randall stadium in madison, wisconsin. mark hoffman/milwaukee journal sentinel\nhometown: waco, texas\n\n\n \n\nfreshman nick evers (transfer)\n\n\nwisconsin quarterback nick evers (7) is shown during practice tuesday, april 11, 2023 at camp randall stadium in madison, wisconsin. mark hoffman-usa today sports\nhometown: flower mound, texas\n\n\n\n\n\n\n \n\nfreshman braedyn locke (transfer)\n\n\nwisconsin quarterback braedyn locke runs an option play as coach luke fickell watches dur

" the super bowl xxxii-winning team in 2022.\nthe second-most recent team to win back-to-back super bowls, the 1998 squad may have been one of the most impressive teams in denver history. in the regular season, the broncos boasted the second-highest scoring offense in the nfl, along with the eighth-ranked defense. running back terrell davis rushed for over 2,000 yards, kicker jason elam tied the then-nfl record with a 63-yard field goal, the team started the season 13-0, and denver finished the regular season at an impressive 14-2 record.\nin the postseason, the broncos cruised past the miami dolphins in the divisional round before winning a nail-biter of a game in the afc championship against the new york jets, 23-10. in the super bowl, denver completely dismantled their nfc foes, the atlanta falcons, 34-19. quarterback john elway retired following the season, capping a hall of fame career.\nalso part of the weekend will be honoring the hall of fame induction of defensive end demarcus

"s-live-stream-tv-channel-start-time-odds-june-20\t\t\t\n\n\n\n\n\n\n\n\n\n\ndata skrive \n\n\n\njune 20, 2023 3:12 am et\n\n\n\n\n\n\n\n\n\nronald acuna jr. and kyle schwarber will be among the stars on display when the atlanta braves face the philadelphia phillies on tuesday at 6:40 pm et, at citizens bank park.\nthe 9.6 strikeouts per nine innings compiled by the braves pitching staff leads mlb. phillies pitchers have a combined era of 4.31 era this year, which ranks 17th in mlb.\nbefore this braves vs. phillies matchup, here's everything you need to prepare for tuesday's mlb action, including viewing options.\nbraves vs. phillies: live streaming info, tv channel & game time\n\ngame day: tuesday, june 20, 2023\ngame time: 6:40 pm et\nlocation: philadelphia, pennsylvania\nstadium: citizens bank park\ntv channel: mlb.tv\nlive stream: fubo (watch for free)\n\nbraves vs. phillies odds & betting lines\n\nfavorite: braves (-145, bet $145 to win $100)\nunderdog: phillies (+123, bet $100 to

's apparently ok with davis (h/t lakers nation).\nvia sportsnaut:\n"lebron james\' optimism about his nba title chances will largely center on how well the lakers continue to build a roster around him and anthony davis. toward the end of the 2022-23 season, cbs sports reported that james had soured on davis for his play and his checkered injury history. a person familiar with james\' thinking, however, stressed that james only has felt upset with davis\' various circumstances as opposed to him personally.\n"\'lebron is not frustrated with ad. lebron is thankful for ad,\' the person told sportsnaut. \'does he wish that both could play and stay healthy the whole time? of course. but it\'s not like he wants a guy to go out there and get injured.\'\n"the person added that lebron james has felt increasingly encouraged with davis for improving his play and durability as the lakers advanced to the western conference finals as a no. 7 seed. that gives james some relative hope that both he and 

In [109]:
#text2find_rex = rex.compile(r'[\n]+')
text2find_rex02 = rex.compile(r'like this article\?')
text2find_rex02 = rex.compile(r'like this article\?[\n]+')
text2find_rex02 = rex.compile(r'like this article\?[\n]+sign[(up)|(for)|(the)|\s]+\s')
text2find_rex02 = rex.compile(r'like this article\?[\n]+sign[(up)|(for)|(the)|\s]+\s[\w\s]*newsletter to get our top stories in your inbox every morning[\n,\s,\t]')
#[\w\s]*newsletter to get our top stories in your inbox every morning[\n,\s,\t]')

#'+email[\n,\s,\t]+sign up[\n,\s,\t]+view all newsletters[\n,\s,\t]+more how to watch'
#text2find_rex02 = rex.compile(r'\d\.\d')

test_lst02 = []
#rpl_lst = []

def test02(text):
    if text2find_rex02.findall(text) == []:
        pass
    else:
        test_lst02.append(text2find_rex02.findall(text))
        #rpl_lst.append(text2find_rex02.sub(lambda match: match.group(0) + ' ', text))
    
slct_tbl_full_df03['norm'].apply(test02)

#display(slct_tbl_full_df03.head())
print(len(test_lst02[:]))
print(test_lst02[:])
#print(rpl_lst[:20])

5157
[['like this article?\nsign up for the tar heels wire newsletter to get our top stories in your inbox every morning\n'], ['like this article?\nsign up for the roll tide wire newsletter to get our top stories in your inbox every morning\n'], ['like this article?\nsign up for the celtics wire newsletter to get our top stories in your inbox every morning\n'], ['like this article?\nsign up for the lebron wire newsletter to get our top stories in your inbox every morning\n'], ['like this article?\nsign up for the roll tide wire newsletter to get our top stories in your inbox every morning\n'], ['like this article?\nsign up for the eagles wire newsletter to get our top stories in your inbox every morning\n'], ['like this article?\nsign up for the trojans wire newsletter to get our top stories in your inbox every morning\n'], ['like this article?\nsign up for the steelers wire newsletter to get our top stories in your inbox every morning\n'], ['like this article?\nsign up for the rams wi

### Lemmatization using spaCY

In [ ]:
nlp_trans = spacy.load('en_core_web_sm')

def lemma(text):
    trans_txt = nlp_trans(text)
    tokens = [t.lemma_ for t in trans_txt]
    return tokens

#### Display globally unqiue tokens on lemmas

In [ ]:
#uniq_tok(df_col=slct_tbl_full_df03['lemma'])

### Split text

#### Apply

In [ ]:
slct_tbl_full_df03['split'] = slct_tbl_full_df03['w_one_return']\
.apply(str.split)

In [ ]:
print(slct_tbl_full_df03.shape)
display(slct_tbl_full_df03.head())

for c in range(0,1):
    try:
        print(slct_tbl_full_df03['split'][c], '\n')
    except:
        print(f'Skip {c}')

#### Display globablly unqiue tokens on first split

In [ ]:
#uniq_tok(df_col=slct_tbl_full_df03['split'])

### Remove stop words

In [ ]:
sw = stopwords.words("english")

# Add additional stop words
sw.extend(['',
           '️',
           'arent',
           'cannot',
           'cant',
           'couldnt',
           'couldve',
           'didnt',
           'doesnt',
           'dont',
           'hadnt',
           'hasnt',
           'havent',
           'hes',
           'im',
           "i'm",
           'isnt',
           'it’s',
           'ive',
           '𝚘𝚏',
           'mightnt',
           'mustnt',
           'neednt',
           'shant',
           'shes',
           'shouldnt',
           'shouldve',
           'thatll',
           'theyll',
           'theyve',
           'wasnt',
           'werent',
           'whats',
           'weve',
           'wont',
           'wouldnt',
           'wouldve',
           'yall',
           'youd',
           'youll',
           'youre',
           'youve',
           "we'll",
           "you’re",
           "you’ve",
           "you’ll",
           "you’d",
           "she’s",
           "it’s",
           "that’ll",
           "don’t",
           "should’ve",
           "aren’t",
           "couldn’t",
           "didn’t",
           "doesn’t",
           "hadn’t",
           "hasn’t",
           "haven’t",
           "isn’t",
           "mightn’t",
           "mustn’t",
           "needn’t",
           "shan’t",
           "shouldn’t",
           "wasn’t",
           "weren’t",
           "won’t",
           "wouldn’t",
           "i’m",
           "we’ll",
           'said',
           'told',
           'according',
           'fox',
           'news',
           'cnn',
           'breitbart',
           'reuters',
           'reporting',
           'reported',
           'statement',
           'spoke',
           'next',
           'though',
           'often',
           'story',
           'updated',
           'additional',
           'developments',
           'follow',
           'published',
          ])

print(sw)

#### Create function

In [ ]:
def sw_remover(tokens):
    return [t for t in tokens if t.lower() not in sw]

#### Call function

In [ ]:
slct_tbl_full_df03['no_sw'] = slct_tbl_full_df03['split'].apply(sw_remover)

In [ ]:
print(slct_tbl_full_df03.shape)
display(slct_tbl_full_df03.head())

for c in range(0,1):
    print(slct_tbl_full_df03['no_sw'][c])

#### Display no stop words

In [ ]:
#uniq_tok(df_col=slct_tbl_full_df03['no_sw'])

### Rejoin semi-processed tokens

In [ ]:
slct_tbl_full_df03['no_sw_join'] = slct_tbl_full_df03['no_sw'].apply(" ".join)

In [ ]:
print(slct_tbl_full_df03.shape)
display(slct_tbl_full_df03.head())

for c in range(0,1):
    print(slct_tbl_full_df03['no_sw_join'][c])

### Remove punctuation

In [ ]:
punctuation = set(punctuation) # speeds up comparison
#print(punctuation)

# Add special hyphen mark
tw_punct = punctuation - {"#"}
#print(tw_punct)

# Remove hash and at symbols for later capture of hashtag info
tw_punct = tw_punct - {"@"}
tw_punct = tw_punct - {"-"}
#tw_punct = tw_punct - {"/"}
tw_punct.add("’")
tw_punct.add("‘")
tw_punct.add("”")
tw_punct.add("“")
tw_punct.add("…")
tw_punct.add("—")
tw_punct.add("...")
tw_punct.add("€")
tw_punct.add("±")
tw_punct.add("£")
tw_punct.add("¡")
tw_punct.add("§")
tw_punct.add("⦿")

print(tw_punct)

#### Create function

In [ ]:
def remove_punctuation(text, punct_set=tw_punct): 
    return("".join([ch for ch in text if ch not in punct_set]))

#### Call function

In [ ]:
slct_tbl_full_df03['no_sw_join_no_punc'] = slct_tbl_full_df03['no_sw_join']\
.apply(remove_punctuation, punct_set=tw_punct)

In [ ]:
print(slct_tbl_full_df03.shape)
display(slct_tbl_full_df03.head())

for c in range(0,1):
    try:
        print(slct_tbl_full_df03['no_sw_join_no_punc'][c], '\n')
    except:
        print(f'\nerror on {c}\n')

### Tokenize

In [ ]:
slct_tbl_full_df03['no_sw_join_no_punc_tok'] = slct_tbl_full_df03['no_sw_join_no_punc'].apply(str.split)

print(slct_tbl_full_df03.shape)
display(slct_tbl_full_df03.head())

for c in range(0,1):
    print(slct_tbl_full_df03['no_sw_join_no_punc_tok'][c], '\n')

#### Display globally unqiue tokens on final tokens

In [ ]:
#uniq_tok(df_col=slct_tbl_full_df03['no_sw_join_no_punc_tok'])

### Pipeline consolidation

#### Pipeline function

In [ ]:
def prepare(text, pipeline):
    '''Run a pipeline of text processing transformers'''
    tokens = str(text)
    
    # Pull key and val from trans dictionaries
    for transformer in pipeline:
        trans = list(transformer.keys())[0]
        args = list(transformer.values())[0]
        #print(trans)
        #print(args)
        if args == None:
            #print(1)
            tokens = trans(tokens)
        else:
            #print('check99', trans, args)
            tokens = trans(tokens, args) 

    return(tokens)

#### `article_text` preprocessing - w/o lemmatization

In [ ]:
'''Set transformer pipeline 1:
Caseloading, normalization (using textacy), special ch removal,
split on whitespace, stop word removal, rejoin,
remove custom punctuation, tokenize
'''
transformers01 = [{str.lower: None},
                  {normalize: None},
                  {rex_replace: None},
                  {remove_url: None},
                  {emoji_split: None},
                  {str.split: None},
                  {sw_remover: None},
                  {" ".join: None},
                  {remove_punctuation: tw_punct},
                  {str.split: None},
                  {" ".join: None},
                 ]

# Apply transformers to pandas dataframe, w/ new col containing tokens
slct_tbl_full_df04['processed_text'] = slct_tbl_full_df04['article_text']\
.progress_apply(prepare, pipeline=transformers01)

slct_tbl_full_df04['processed_text_split'] = slct_tbl_full_df04['processed_text']\
.progress_apply(str.split)

slct_tbl_full_df04['num_tokens'] = slct_tbl_full_df04['processed_text_split']\
.map(len)

display(slct_tbl_full_df04.head())

# Review unique tokens across entire dataset
for c in range(0,1):
    try:
        print(slct_tbl_full_df04['processed_text'][c], '\n')
    except:
        print(f'Skip {c}')

##### Display globally unqiue tokens on final tokens

In [ ]:
#uniq_tok(df_col=slct_tbl_full_df04['processed_text_split'])

#### `article_text` preprocessing - w/ lemmatization

##### Display globally unqiue tokens on final tokens

#uniq_tok(df_col=slct_tbl_full_df04['processed_lemmas_split'])

### Train/test split

In [ ]:
slct_tbl_full_df04['stratifier'] = slct_tbl_full_df04['political_lean']\
.astype(str) + slct_tbl_full_df04['source_name'].astype(str)
slct_tbl_full_df04['stratifier'] = slct_tbl_full_df04['stratifier']\
.map(str.lower)
display(slct_tbl_full_df04.head())

y01a = ['stratifier']
slct_tbl_full_df04_y01_vc01a = slct_tbl_full_df04[y01a].to_numpy()
print(slct_tbl_full_df04_y01_vc01a.shape)

y01 = ['political_lean']
slct_tbl_full_df04_y01_vc01 = slct_tbl_full_df04[y01].to_numpy()
print(slct_tbl_full_df04_y01_vc01.shape)

In [ ]:
nlm_train_x01, \
nlm_test_x01, \
nlm_train_y01, \
nlm_test_y01 = train_test_split(slct_tbl_full_df04['processed_text'],
                                slct_tbl_full_df04_y01_vc01,
                                test_size=.15,
                                random_state=1699,
                                stratify=slct_tbl_full_df04_y01_vc01a
                               )

nlm_train_y01 = nlm_train_y01.ravel()
nlm_test_y01 = nlm_test_y01.ravel()

print(f'{nlm_train_x01.shape}')
print(f'{nlm_train_y01.shape}')
print(f'\n{nlm_test_x01.shape}')
print(f'{nlm_test_y01.shape}')

### BERTopic

In [ ]:
print(len(slct_tbl_full_df04['processed_text']))
display(slct_tbl_full_df04['processed_text'].head())

'''
BERTopic citation
https://chat.openai.com/share/04f961fa-14f3-4bfb-b7ed-f71f9ebaee65'''
# Read the dataset into a pandas DataFrame
#df = pd.read_csv('your_data.csv')

# Extract the column containing the unstructured text
documents = slct_tbl_full_df04['processed_text']

# Train BERTopic on the text column
model = BERTopic(ngram_range=(1,3))
topics, _ = model.fit_transform(documents)

# Assign topics to records and generate labels
k = 3  # Number of words to select as labels per record
labels_per_record = []
for record_topics in topics:
    record_labels = []
    for topic_id in record_topics:
        topic_words = model.get_topic(topic_id)[:k]
        record_labels.extend(topic_words)
    labels_per_record.append(record_labels)

# Print labels for each record
for i, labels in enumerate(labels_per_record):
    print(f"Record {i+1}: {labels}")


### TF-IDF

In [ ]:
print(slct_tbl_full_df04['processed_text'].shape)
print(slct_tbl_full_df04['processed_text'].head())

In [ ]:
nlm_tfidf = TfidfVectorizer(encoding='utf-8',
                            analyzer='word',
                            stop_words=sw,
                            token_pattern=r'(?u)\b\w\w+\b',
                            ngram_range=(1,3),
                            max_df=.7,
                            min_df=5)

nlm_train_x01_mtx = nlm_tfidf.fit_transform(nlm_train_x01)
nlm_test_x01_mtx = nlm_tfidf.transform(nlm_test_x01)

display(nlm_train_x01_mtx)
display(nlm_test_x01_mtx)

In [ ]:
def display_samp_dwm(sm=None,
                     vec=None,
                     n=(1,1),
                     rs_tup=(1,1)):
    mtx_df01 = pd.DataFrame(sm.toarray(),
                            columns=vec.get_feature_names_out())

    mtx_df01a = mtx_df01.sample(n=n[0],
                                random_state=rs_tup[0],
                                axis=1)

    mtx_df01b = mtx_df01a.sample(n=n[1],
                                 random_state=rs_tup[1],
                                 axis=0)

    display(mtx_df01b)
    return vec.get_feature_names_out()

In [ ]:
rs_tup=(1699,1699)

In [ ]:
nlm_train_x01_mtx_cols = display_samp_dwm(sm=nlm_train_x01_mtx,
                                          vec=nlm_tfidf,
                                          n=(17,11),
                                          rs_tup=(5,1699))

display_samp_dwm(sm=lem_train_x01_mtx,
                 vec=lem_tfidf,
                 n=(17,11),
                 rs_tup=(5,1699))

## Modeling

### Algorithm setup

### Gradient Boosting Classifier - Using `BayesSearchCV`

### Pickle best model

In [ ]:
# Path to save the pickled model
mod_folder_name = 'trained_models'
m2v1_pkl_file_name = 'm2v2_gbc.pkl'

pkl_file_path01 = os.path.join(curr_dir, mod_folder_name, m2v1_pkl_file_name)

print(f'CSV file 1 in path: {pkl_file_path01}')

### Load pickled best model

In [ ]:
with open(pkl_file_path01, 'rb') as file:
    m2v1_gbc = pickle.load(file)

In [ ]:
print(f'\nBest Estimator:\n{m2v1_gbc.best_estimator_}')

print('\nCross-validaton results:')
display(pd.DataFrame(m2v1_gbc.cv_results_))

train_m2v1_gbc_y01_pred = m2v1_gbc.predict_proba(nlm_train_x01_mtx)
print(f'\nFirst 10 train set predictions:\n{train_m2v1_gbc_y01_pred[:10]}')

test_m2v1_gbc_y01_pred = m2v1_gbc.predict_proba(nlm_test_x01_mtx)
print(f'\nFirst 10 test set predictions:\n{test_m2v1_gbc_y01_pred[:10]}')

print(f'\nBest Score for "{m2v1_gbc.scorer_}" is {m2v1_gbc.best_score_}')

#### Train set check

In [ ]:
nlm_train_y01_pred = m2v1_gbc.predict(nlm_train_x01_mtx)
nlm_train_y01_pred_cm = confusion_matrix(nlm_train_y01, nlm_train_y01_pred)

print(classification_report(nlm_train_y01, nlm_train_y01_pred))
print(nlm_train_y01_pred_cm)

'''Citation:
https://scikit-learn.org/stable/modules/generated
/sklearn.metrics.ConfusionMatrixDisplay.html
#sklearn.metrics.ConfusionMatrixDisplay.plot
'''
nlm_train_cm_dsp = ConfusionMatrixDisplay(confusion_matrix=nlm_train_y01_pred_cm,
                                          display_labels=m2v1_gbc.classes_)
nlm_train_cm_dsp.plot()
plt.show()

#### ROC-AUC Curve

In [ ]:
nlm_train_y01_pred_decf = m2v1_gbc.decision_function(nlm_train_x01_mtx)
RocCurveDisplay.from_predictions(nlm_train_y01, nlm_train_y01_pred_decf,
                                 pos_label='right')
plt.show()

#### Test set results

In [ ]:
nlm_test_y01_pred = m2v1_gbc.predict(nlm_test_x01_mtx)
nlm_test_y01_pred_cm = confusion_matrix(nlm_test_y01, nlm_test_y01_pred)

print('Test Set Evaluation Metrics')
print(classification_report(nlm_test_y01, nlm_test_y01_pred))
print(nlm_test_y01_pred_cm)

'''Citation:
https://scikit-learn.org/stable/modules/generated
/sklearn.metrics.ConfusionMatrixDisplay.html
#sklearn.metrics.ConfusionMatrixDisplay.plot
'''
nlm_test_cm_dsp = ConfusionMatrixDisplay(confusion_matrix=nlm_test_y01_pred_cm,
                                         display_labels=m2v1_gbc.classes_)
nlm_test_cm_dsp.plot()
plt.show()

#### Variable importance

In [ ]:
print(nlm_train_x01_mtx_cols)
print(type(nlm_train_x01_mtx_cols))
print(nlm_train_x01_mtx_cols.shape)

x = m2v1_gbc.best_estimator_.named_steps['gbc'].feature_importances_
x_df01 = pd.DataFrame(x, columns=['var_imp'])
x_df01['feature'] = nlm_train_x01_mtx_cols
x_df02 = x_df01.sort_values(by=['var_imp'], ascending=False)
x_df03 = x_df02.head(20)

display(x_df02.head())
print(type(x_df02))
print(x_df02.shape)

In [ ]:
'''Citation:
https://machinelearningmastery.com/calculate-feature-importance-with-python/
'''
# plot feature importance
#figure = plt.figsize((10,9))
plt.figure(figsize=(15,7))
plt.title('Feature Importance (Top 20)')
plt.barh([x for x in range(len(x_df03['var_imp']))], x_df03['var_imp'],
         tick_label=x_df03['feature'])
plt.show()

In [ ]:
TNmodel1=nlm_test_y01_pred_cm[0][0]
FPmodel1=nlm_test_y01_pred_cm[0][1]
FNmodel1=nlm_test_y01_pred_cm[1][0]
TPmodel1=nlm_test_y01_pred_cm[1][1]

In [ ]:
# Results:
from tabulate import tabulate

TANmodel1=TNmodel1+FPmodel1
TAPmodel1=TPmodel1+FNmodel1
TPPmodel1=FPmodel1+TPmodel1
TPNmodel1=TNmodel1+FNmodel1
GTmodel1=TANmodel1+TAPmodel1
AccuracyM1=(TNmodel1+TPmodel1)/GTmodel1
ErrorRateM1=1-AccuracyM1
SensitivityM1=TPmodel1/(TAPmodel1)
RecallM1=SensitivityM1
SpecificityM1=TNmodel1/TANmodel1
PrecisionM1=TPmodel1/TPPmodel1
F1M1=2*PrecisionM1*RecallM1/(PrecisionM1 + RecallM1)
F2M1=5*(PrecisionM1*RecallM1)/((4*PrecisionM1)+RecallM1)
Fp5M1=(1.25)*(PrecisionM1*RecallM1)/((0.25*PrecisionM1)+RecallM1)

header = ["Accuracy", "Error Rate", "Sensitivity", "Recall", "Specificity",
          "Precision", "F1", "F2", "F0.5"]
data1 = [["Accuracy", AccuracyM1], ["Error Rate", ErrorRateM1],
         ["Sensitivity", SensitivityM1],
         ["Recall", RecallM1], ["Specificity", SpecificityM1],
         ["Precision", PrecisionM1],
         ["F1", F1M1], ["F2", F2M1], ["F0.5", Fp5M1]]

col_names=["Measurement", "Linear SVC Model"]

ModelEvaluationTable = tabulate(data1, headers=col_names,
                                tablefmt="fancy_grid")

print(ModelEvaluationTable)

In [ ]:
data1

In [ ]:
Data_metric_results_TheHill=pd.DataFrame(data1)
Data_metric_results_TheHill.head()

In [ ]:
Data_metric_results_TheHill.rename (columns = {0:'Measurement'}, inplace=True) 
Data_metric_results_TheHill.rename (columns = {1:'Result'}, inplace=True) 

In [ ]:
#plt.bar(x=ModelEvaluationTable)
ax=Data_metric_results_TheHill[(Data_metric_results_TheHill['Measurement'] == 'Accuracy') | 
                            (Data_metric_results_TheHill['Measurement'] == 'Recall') |
                            (Data_metric_results_TheHill['Measurement'] == 'F1') |
                            (Data_metric_results_TheHill['Measurement'] == 'Error Rate')].plot(kind="barh", 
                                                                                               x='Measurement',
                                  figsize=(5,6),
                                  title='Linear SVC Performance metrics on Test Data')
ax.bar_label(ax.containers[0])
ax.set_xlim(right=1.15)

## Business problem application

In [ ]:
center_df01 = pd.read_csv(file_in_path02)

print(center_df01.shape)
display(center_df01.head())

In [ ]:
# Apply transformers to pandas dataframe, w/ new col containing tokens
center_df01['processed_text'] = center_df01['article_text']\
.progress_apply(prepare, pipeline=transformers01)

center_df01['processed_text_split'] = center_df01['processed_text']\
.progress_apply(str.split)

center_df01['num_tokens'] = center_df01['processed_text_split']\
.map(len)

display(center_df01.head())

# Review unique tokens across entire dataset
for c in range(0,1):
    try:
        print(center_df01['processed_text'][c], '\n')
    except:
        print(f'Skip {c}')

In [ ]:
nlm_apply_x01_mtx = nlm_tfidf.transform(center_df01['processed_text'])

print(nlm_apply_x01_mtx.shape)
display(nlm_apply_x01_mtx)

In [ ]:
display_samp_dwm(sm=nlm_apply_x01_mtx,
                 vec=nlm_tfidf,
                 n=(17,11),
                 rs_tup=(5,1699))

In [ ]:
nlm_apply_mtx_pred_prob = m2v1_gbc.predict_proba(nlm_apply_x01_mtx)

print(nlm_apply_mtx_pred_prob.shape)
print(nlm_apply_mtx_pred_prob[:10])

nlm_apply_mtx_pred = m2v1_gbc.predict(nlm_apply_x01_mtx)

print(nlm_apply_mtx_pred.shape)
print(nlm_apply_mtx_pred)

In [ ]:
# Compute the maximum values along the second dimension
max_values = np.amax(nlm_apply_mtx_pred_prob, axis=1)
max_values_df01 = pd.DataFrame(max_values,
                               columns=['decision_prob'])
max_values_df01['pred'] = nlm_apply_mtx_pred
print(max_values_df01.shape)
display(max_values_df01.head())

In [ ]:
max_values_df01['decision_prob'].plot(kind="hist",
                                      density=True,
                                      alpha=0.5,
                                      legend=True,
                                      figsize=(10,7),
title='''Gradient Boost Model Probability Distribution\n
                                      Applied to Customer Articles''')

In [ ]:
max_values_df01.groupby('pred')['decision_prob'].plot(kind="hist",
                                                      density=True,
                                      alpha=0.5,
                                      legend=True,
                                      figsize=(10,7),
                          title='''Gradient Boost Model Probability Distribution
Prediction Confidence''')

In [ ]:
max_values_df02 = pd.DataFrame(nlm_apply_mtx_pred_prob.round(4),
                               columns=['left', 'right'])
max_values_df02['pred'] = nlm_apply_mtx_pred
max_values_df02

In [ ]:
# Plotting histograms
#plt.hist(max_values_df02['left'], bins=10, alpha=0.5, color='blue', label='Column 1')
plt.hist(max_values_df02['right'], bins=10, alpha=0.5, color='red',
         label='right')

# Adding legend and title
plt.legend()
plt.title('Histogram of Right Prediction Probabilities')

# Displaying the plot
plt.show()

In [ ]:
# Plotting histograms
#plt.hist(max_values_df02['left'], bins=10, alpha=0.5, color='blue', label='Column 1')
plt.hist(max_values_df02['left'], bins=10, alpha=0.5, color='blue',
         label='left')

# Adding legend and title
plt.legend()
plt.title('Histogram of Left Prediction Probabilities')

# Displaying the plot
plt.show()

In [ ]:
# Plotting histograms
plt.hist(max_values_df02['left'], bins=10,
         alpha=0.5, color='blue', label='left')
plt.hist(max_values_df02['right'], bins=10,
         alpha=0.5, color='red', label='right')

# Adding legend and title
plt.legend()
plt.title('Histogram of Left/Right Prediction Probabilities')

# Displaying the plot
plt.show()